# This notebook its implemented to match real contract object with the extracted one. Creating new dataframe with both columns and extra metadata of the related contract

In [2]:
!pip install --upgrade pandas

  Using cached pandas-2.2.3-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (89 kB)
Using cached pandas-2.2.3-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (13.1 MB)
  Attempting uninstall: pandas
    Found existing installation: pandas 2.2.2
    Uninstalling pandas-2.2.2:
      Successfully uninstalled pandas-2.2.2


In [3]:
import pandas as pd
import requests
import time
from tqdm import tqdm
import os

In [4]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

In [9]:
path1 = '/export/data_ml4ds/NextProcurement/PLACE/pliegos_objectives/all_extracted_12aug_es/all_extracted_12aug_es_4_objectives.parquet'

df_PLACE_ins = pd.read_parquet('/export/usuarios_ml4ds/cggamella/NP-Company-Process/data/DESCARGAS_MAYO/insiders.parquet')
df_PLACE_out = pd.read_parquet('/export/usuarios_ml4ds/cggamella/NP-Company-Process/data/DESCARGAS_MAYO/outsiders.parquet')
df_PLACE_min = pd.read_parquet('/export/usuarios_ml4ds/cggamella/NP-Company-Process/data/DESCARGAS_MAYO/minors.parquet')

df_extracted = pd.read_parquet(path1)

In [10]:
df_PLACE_out['origin'] = 'out'
df_PLACE_ins['origin'] = 'ins'
df_PLACE_min['origin'] = 'min'

In [11]:
def unify_colname(col):
    return ".".join([el for el in col if el])

In [12]:
df_PLACE_ins = df_PLACE_ins.rename(columns={"id":"place_id"})
df_PLACE_min = df_PLACE_min.rename(columns={"id":"place_id"})
df_PLACE_out = df_PLACE_out.rename(columns={"id":"place_id"})

In [13]:
df_PLACE_out.columns = [unify_colname(col) for col in df_PLACE_out.columns]
df_PLACE_ins.columns = [unify_colname(col) for col in df_PLACE_ins.columns]
df_PLACE_min.columns = [unify_colname(col) for col in df_PLACE_min.columns]

In [25]:
def obtener_id_place(procurement_id_x):
    url_base = "https://nextprocurement.bsc.es/api/place/"
    url_fallback = "https://nextprocurement.bsc.es/api/place_menores/"
    url_completa = f"{url_base}{procurement_id_x}/id"
    url_completa_fallback = f"{url_fallback}{procurement_id_x}/id"
    
    try:
        print(f"Solicitando ID para {procurement_id_x} con URL principal...")
        response = requests.get(url_completa)
        
        if response.status_code == 200:
            data = response.json()
            print("El json completo es:", data)  
            place_id = data.get('id')
            print("ID obtenido:", place_id)  
            return place_id
        else:
            print("Respuesta no exitosa con la URL principal. Código de estado:", response.status_code)
    
    except Exception as e:
        print("Excepción durante la solicitud con la URL principal:", str(e))

    try:
        print(f"Solicitando ID para {procurement_id_x} con URL menores...")
        response = requests.get(url_completa_fallback)
        
        if response.status_code == 200:
            data = response.json()
            print("El json completo es:", data)  
            place_id = data.get('id')
            print("ID obtenido:", place_id)  
            return place_id
        else:
            print("Respuesta no exitosa con la URL menores. Código de estado:", response.status_code)
    
    except Exception as e:
        print("Excepción durante la solicitud con la URL secundaria:", str(e))

    print("No se pudo obtener el ID ni con la URL principal ni con la de menores.")
    return None

In [26]:
df_extracted['place_id'] = [obtener_id_place(x) for x in tqdm(df_extracted['procurement_id_x'])]

  0%|                                                                                                             | 2/10000 [00:00<09:27, 17.61it/s]

Solicitando ID para ntp01347849... Intento 1
El json completo es: {'_id': 'ntp01347849', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12656825'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12656825
Solicitando ID para ntp01005550... Intento 1
El json completo es: {'_id': 'ntp01005550', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/10906096'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/10906096
Solicitando ID para ntp00833944... Intento 1
El json completo es: {'_id': 'ntp00833944', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/8185322'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/8185322
Solicitando ID para ntp01301925... Intento 1


  0%|                                                                                                             | 6/10000 [00:00<09:19, 17.87it/s]

El json completo es: {'_id': 'ntp01301925', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/10344540'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/10344540
Solicitando ID para ntp01334091... Intento 1
El json completo es: {'_id': 'ntp01334091', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12267745'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12267745
Solicitando ID para ntp01309074... Intento 1
El json completo es: {'_id': 'ntp01309074', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12011543'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12011543
Solicitando ID para ntp00589490... Intento 1
El json completo es: {'_id': 'ntp00589490', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/1192813'}
ID obtenido: https://contra

  0%|                                                                                                            | 10/10000 [00:00<11:52, 14.03it/s]

...

El json completo es: {'_id': 'ntp00485257', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/2471182'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/2471182
Solicitando ID para ntp00512725... Intento 1
El json completo es: {'_id': 'ntp00512725', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/2338285'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/2338285
Solicitando ID para ntp00836072... Intento 1
El json completo es: {'_id': 'ntp00836072', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/8322509'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/8322509
Solicitando ID para ntp01313076... Intento 1
El json completo es: {'_id': 'ntp01313076', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/13128610'}
ID obtenido: https://contratacio

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 9995/10000 [09:45<00:00, 19.81it/s]

El json completo es: {'_id': 'ntp00583738', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/4229736'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/4229736
Solicitando ID para ntp01295237... Intento 1
El json completo es: {'_id': 'ntp01295237', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12041818'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12041818
Solicitando ID para ntp01371614... Intento 1
El json completo es: {'_id': 'ntp01371614', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/13363645'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/13363645
Solicitando ID para ntp00437626... Intento 1
El json completo es: {'_id': 'ntp00437626', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/1854489'}
ID obtenido: https://contrata

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████| 10000/10000 [09:45<00:00, 17.08it/s]

El json completo es: {'_id': 'ntp00598305', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/4126945'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/4126945
Solicitando ID para ntp00082708... Intento 1
El json completo es: {'_id': 'ntp00082708', 'id': 'https://contrataciondelestado.es/sindicacion/PlataformasAgregadasSinMenores/2371067'}
ID obtenido: https://contrataciondelestado.es/sindicacion/PlataformasAgregadasSinMenores/2371067
Solicitando ID para ntp01150248... Intento 1
El json completo es: {'_id': 'ntp01150248', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12518503'}
ID obtenido: https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/12518503
Solicitando ID para ntp00575585... Intento 1
El json completo es: {'_id': 'ntp00575585', 'id': 'https://contrataciondelestado.es/sindicacion/licitacionesPerfilContratante/4131650'}
ID obtenido: https://contrata

In [27]:
mapeo_nuts_ccaa = {
    11: "Galicia",
    12: "Principado de Asturias",
    13: "Cantabria",
    21: "Pais Vasco",
    22: "Comunidad Foral de Navarra",
    23: "La Rioja",
    24: "Aragon",
    30: "Comunidad de Madrid",
    41: "Castilla y Leon",
    42: "Castilla-La Mancha",
    43: "Extremadura",
    51: "Cataluña",
    52: "Comunitat Valenciana",
    53: "Illes Balears",
    61: "Andalucia",
    62: "Region de Murcia",
    63: "Ciudad de Ceuta",
    64: "Ciudad de Melilla",
    70: "Canarias"
}

mapeo_nuts_provincia = {
    111: "A Coruña",
    112: "Lugo",
    113: "Ourense",
    114: "Pontevedra",
    120: "Asturias",
    130: "Cantabria",
    211: "Araba/Álava",
    212: "Gipuzkoa",
    213: "Bizkaia",
    220: "Navarra",
    230: "La Rioja",
    241: "Huesca",
    242: "Teruel",
    243: "Zaragoza",
    300: "Madrid",
    411: "Avila",
    412: "Burgos",
    413: "León",
    414: "Palencia",
    415: "Salamanca",
    416: "Segovia",
    417: "Soria",
    418: "Valladolid",
    419: "Zamora",
    421: "Albacete",
    422: "Ciudad Real",
    423: "Cuenca",
    424: "Guadalajara",
    425: "Toledo",
    431: "Badajoz",
    432: "Cáceres",
    511: "Barcelona",
    512: "Girona",
    513: "Lleida",
    514: "Tarragona",
    521: "Alicante",
    522: "Castellón",
    523: "Valencia",
    531: "Ibiza y Formentera",
    532: "Mallorca",
    533: "Menorca",
    611: "Almería",
    612: "Cádiz",
    613: "Córdoba",
    614: "Granada",
    615: "Huelva",
    616: "Jaén",
    617: "Málaga",
    618: "Sevilla",
    620: "Murcia",
    630: "Ceuta",
    640: "Melilla",
    704: "Fuerteventura",
    705: "Gran Canaria",
    708: "Lanzarote",
    703: "El Hierro",
    706: "La Gomera",
    707: "La Palma",
    709: "Tenerife"
}

In [15]:
columns_keep_ins_min = [
    'ContractFolderStatus.ProcurementProject.RequiredCommodityClassification.ItemClassificationCode', #CPV
    'ContractFolderStatus.ProcurementProject.RealizedLocation.CountrySubentityCode', # Ciudad NUTS
    'ContractFolderStatus.LocatedContractingParty.ParentLocatedParty.PartyName.Name', #Ubicación orgánica
    'ContractFolderStatus.ProcurementProject.BudgetAmount.EstimatedOverallContractAmount', #Presupuesto
    'ContractFolderStatus.TenderResult.SMEAwardedIndicator', #Es pyme
    'ContractFolderStatus.ContractFolderID', #Expediente
    'title', #Título de PLACE
    'ContractFolderStatus.ValidNoticeInfo.AdditionalPublicationStatus.AdditionalPublicationDocumentReference.IssueDate', #Fecha
    'origin',
    'place_id'
]
# En outsiders no se determina si es PYME o no.
columns_keep_out = [
    'ContractFolderStatus.ProcurementProject.RequiredCommodityClassification.ItemClassificationCode', #CPV
    'ContractFolderStatus.ProcurementProject.RealizedLocation.CountrySubentityCode', # Ciudad NUTS
    'ContractFolderStatus.LocatedContractingParty.ParentLocatedParty.PartyName.Name', #Ubicación orgánica
    'ContractFolderStatus.ProcurementProject.BudgetAmount.EstimatedOverallContractAmount', #Presupuesto
    'ContractFolderStatus.ContractFolderID', #Expediente
    'title', #Título de PLACE
    'ContractFolderStatus.ValidNoticeInfo.AdditionalPublicationStatus.AdditionalPublicationDocumentReference.IssueDate', #Fecha
    'origin',
    'place_id'
]

In [16]:
df_PLACE_min = df_PLACE_min[columns_keep_ins_min]
df_PLACE_ins = df_PLACE_ins[columns_keep_ins_min]
df_PLACE_out = df_PLACE_out[columns_keep_out]

In [17]:
df_concat = pd.concat([df_PLACE_min, df_PLACE_ins, df_PLACE_out], ignore_index=True)

In [21]:
df_concat.to_parquet('/export/usuarios_ml4ds/cggamella/NP-Text_Object/data/objectives_with_metadata/df_PLACE_completo.parquet')

In [33]:
df_cruce = pd.merge(df_extracted, df_concat, on="place_id", how='inner')
df_cruce

procurement_id_x                                        doc_name  \
0         ntp01347849  ntp01347849_Pliego_Prescripciones_tecnicas_URI   
1         ntp01005550  ntp01005550_Pliego_Prescripciones_tecnicas_URI   
2         ntp00833944  ntp00833944_Pliego_Prescripciones_tecnicas_URI   
3         ntp01301925  ntp01301925_Pliego_Prescripciones_tecnicas_URI   
4         ntp01334091  ntp01334091_Pliego_Prescripciones_tecnicas_URI   
...               ...                                             ...   
9995      ntp00437626  ntp00437626_Pliego_Prescripciones_tecnicas_URI   
9996      ntp00598305  ntp00598305_Pliego_Prescripciones_tecnicas_URI   
9997      ntp00082708  ntp00082708_Pliego_Prescripciones_tecnicas_URI   
9998      ntp01150248  ntp01150248_Pliego_Prescripciones_tecnicas_URI   
9999      ntp00575585  ntp00575585_Pliego_Prescripciones_tecnicas_URI   

     translated                                          extracted  \
0            no  Plaza de la Constitución, 1\n \n 04740 Roqueta...   
1            no  Qïggí—%e} YX\n Eí S MINISTERIO MANDO DE APOYO\...   
2            no  Contacto\nE El '_“M¿ COLEGIO OFICIAL DE ARQUIT...   
3            no  PLIEGO DE CONDICIONES TÉCNICAS Y\nPARTICULARES...   
4            no  NO de expediente: 20/2023\n Tramitación: Ordin...   
...         ...                                                ...   
9995         no  EJÉRCITO DE TIERRA\n— \ MINISTERIO DE MANDO DE...   
9996         no  PLIEGO DE CLÁUSULAS TÉCNICAS PARTICULARES PARA...   
9997         no  Atención Especializada. Area 7.MADRID\n Prof. ...   
9998         no  . . s Z u\n Diputación de Córdoba Sa\n , 7\n A...   
9999         no  DOCUMENTO\n VQ_Pliego técnico: Pliego técnico\...   

                                        clean_extracted      lang  \
0     Plaza de la Constitución, 1 04740 Roquetas de ...  spa_Latn   
1     Qïggí—%e} YX Eí S MINISTERIO MANDO DE APOYO e ...  spa_Latn   
2     Contacto E El '_“M¿ COLEGIO OFICIAL DE ARQUITE...  spa_Latn   
3     PLIEGO DE CONDICIONES TÉCNICAS Y PARTICULARES ...  spa_Latn   
4     NO de expediente: 20/2023 Tramitación: Ordinar...  spa_Latn   
...                                                 ...       ...   
9995  EJÉRCITO DE TIERRA — \ MINISTERIO DE MANDO DE ...  spa_Latn   
9996  PLIEGO DE CLÁUSULAS TÉCNICAS PARTICULARES PARA...  spa_Latn   
9997  Atención Especializada. Area 7.MADRID Prof. Ma...  spa_Latn   
9998  . . s Z u Diputación de Córdoba Sa , 7 Area de...  spa_Latn   
9999  DOCUMENTO VQ_Pliego técnico: Pliego técnico GT...  spa_Latn   

                                              objective  in_text_score  \
0     El objeto del presente contrato es la concesió...       1.000000   
1     El objeto de este Pliego de Prescripciones Téc...       1.000000   
2     La presente documentación tiene por objeto la ...       1.000000   
3     El contrato que se regirá por el presente Plie...       1.000000   
4     El Presente Pliego se atendrá a lo dispuesto e...       1.000000   
...                                                 ...            ...   
9995  El objçto del contrato, es la explotación del ...       1.000000   
9996  El objeto del contrato es la realización de lo...       0.976744   
9997  El objeto del presente contrato es la adquisic...       0.470588   
9998  El camping de Fuente Obejuna se ejecuta a trav...       1.000000   
9999  El objeto del contrato se desarrollará en 4 fa...       0.978261   

      processed_0  processed_1000  ...  \
0            True            True  ...   
1            True            True  ...   
2            True            True  ...   
3            True            True  ...   
4            True            True  ...   
...           ...             ...  ...   
9995         True            True  ...   
9996         True            True  ...   
9997         True            True  ...   
9998         True            True  ...   
9999         True            True  ...   

                                               place_id  \
0    

In [34]:
df_cruce['origin'].value_counts()

origin
ins    7847
out    1457
min     696
Name: count, dtype: int64

In [39]:
import numpy as np

In [40]:
def asignar_ccaa_provincia(df_cruce):
    if 'ContractFolderStatus.ProcurementProject.RealizedLocation.CountrySubentityCode' not in df_cruce.columns:
        raise ValueError("La columna 'ContractFolderStatus.ProcurementProject.RealizedLocation.CountrySubentityCode' no existe en el dataframe.")
    
    def obtener_ccaa(code):
        if pd.isna(code) or code in ['', 'None']:
            return np.nan
        try:
            # Extraer XY de ESXYZ código NUTS
            xy = int(code[2:4])
            return mapeo_nuts_ccaa.get(xy, np.nan)
        except:
            return np.nan
    
    def obtener_provincia(code):
        if pd.isna(code) or code in ['', 'None']:
            return np.nan
        try:
            # Extraer XYZ de ESXYZ
            xyz = int(code[2:5])
            return mapeo_nuts_provincia.get(xyz, np.nan)
        except:
            return np.nan
    
    df_cruce['ccaa'] = df_cruce['ContractFolderStatus.ProcurementProject.RealizedLocation.CountrySubentityCode'].apply(obtener_ccaa)
    df_cruce['provincia'] = df_cruce['ContractFolderStatus.ProcurementProject.RealizedLocation.CountrySubentityCode'].apply(obtener_provincia)

    return df_cruce

In [41]:
df_cruce = asignar_ccaa_provincia(df_cruce)

In [24]:
'''
def concatenar_parquet_y_exportar(input_folder):
    
    dataframes = []
    for file_name in os.listdir(input_folder):
        if file_name.endswith(".parquet"):
            file_path = os.path.join(input_folder, file_name)
            df = pd.read_parquet(file_path)
            dataframes.append(df)
            print(f"Archivo {file_name} leído con éxito.")
    
    # Concatenar todos los DataFrames
    df_concatenado = pd.concat(dataframes, ignore_index=True)
    print("Todos los archivos concatenados correctamente.")
    
    return df_concatenado

input_folder = '/export/data_ml4ds/NextProcurement/PLACE/pliegos_objectives/all_extracted_12aug_es'
output_file = '/export/usuarios_ml4ds/cggamella/RAG_tool/data/NextProcurement/concatenated_output.parquet'

df = concatenar_parquet_y_exportar(input_folder)
'''

Archivo all_extracted_12aug_es_22_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_8_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_10_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_4_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_36_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_33_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_27_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_19_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_15_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_26_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_18_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_14_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_32_objectives.parquet leído con éxito.
Archivo all_extracted_12aug_es_37_objectives.parquet leído con éxito.
Archivo all_extracted_

In [20]:
df = pd.read_parquet('/export/usuarios_ml4ds/cggamella/NP-Text_Object/data/objectives_with_metadata/procesado/all_extracted_12aug_es_4_objectives_processed.parquet')

In [22]:
#df

In [27]:
df.columns

Index(['procurement_id_x', 'doc_name', 'translated', 'extracted',
       'clean_extracted', 'lang', 'objective', 'in_text_score', 'processed_0',
       'processed_1000', 'processed_2000', 'processed_3000', 'processed_4000'],
      dtype='object')

In [23]:
df_filtrado = df[['procurement_id_x','doc_name','objective','in_text_score', 'title']]

In [24]:
len(df_filtrado['in_text_score'])

10000

In [33]:
df_1 = df_filtrado[
    df_filtrado['in_text_score']&
    df_filtrado['objective']!='/'
]

np.float64(0.9784380165893539)

In [49]:
df_1 = df_filtrado[
    (df_filtrado['in_text_score'] > 0.65)
]

In [55]:
len(df_1)

175889

In [53]:
df_2 = df_1[
    (df_1['objective'] != '/')
]

In [54]:
len(df_2)

175889

In [ ]:
#import pandas as pd
#output_file = '/export/usuarios_ml4ds/cggamella/RAG_tool/data/NextProcurement/in_text_score_mas_0_65_y_slash_remove.parquet'
#df_2.to_parquet(output_file)

In [25]:
import pandas as pd
pd.set_option('display.max_colwidth', None)

df = pd.read_parquet("/export/usuarios_ml4ds/cggamella/RAG_tool/data/NextProcurement/in_text_score_mas_0_65_y_slash_remove.parquet")
df

procurement_id_x                                        doc_name  \
0           ntp00464298  ntp00464298_Pliego_Prescripciones_tecnicas_URI   
1           ntp01105292  ntp01105292_Pliego_Prescripciones_tecnicas_URI   
2           ntp01335284  ntp01335284_Pliego_Prescripciones_tecnicas_URI   
3           ntp00443046  ntp00443046_Pliego_Prescripciones_tecnicas_URI   
4           ntp00949665  ntp00949665_Pliego_Prescripciones_tecnicas_URI   
...                 ...                                             ...   
179995      ntp00339574  ntp00339574_Pliego_Prescripciones_tecnicas_URI   
179996      ntp01137937  ntp01137937_Pliego_Prescripciones_tecnicas_URI   
179997      ntp00205207  ntp00205207_Pliego_Prescripciones_tecnicas_URI   
179998      ntp01312540  ntp01312540_Pliego_Prescripciones_tecnicas_URI   
179999      ntp00736588  ntp00736588_Pliego_Prescripciones_tecnicas_URI   

                                                                                                                                                                                                                                                                                                                                             objective  \
0                                                El Pliego de Condiciones Particulares que nos ocupa se extiende a todas las obras que integran el presente "ESTUDIO DE SEGURIDAD Y SALUD", especificadas en el Documento A "MEMORIA", y aquellas obras que estime convenientes el Facultativo que suscribe, para que la ejecución material de la obra   
1                                                              Constituye el objeto de este documento establecer las condiciones técnicas que deberán cumplir los trabajos relativos al “Suministro y entrega de frutas, hortalizas y leche en los centros escolares de la Comunidad Autónoma de la Región de Murcia" para el curso escolar 2022/2023.   
2                               El presente Pliego tiene por objeto recoger las condiciones técnicas básicas por las que se regirá la contratación por parte de la Empresa de Transformación Agraria, S.A., SME, MP, en adelante TRAGSA, de los trabajos derivados de la presente licitación. Dichas condiciones serán de aplicación a la totalidad de   
3                                                                                   calibración de los equipos y su soporte lógico (software), según la Norma 17025 (punto 5.5.2), incluidos en el Anexo, para asegurar el correcto funcionamiento de los equipos que van a ser utilizados en la AEMPS, cumpliendo los requisitos recogidos en los Man   
4                                                                                                                                                                 El objeto del presente contrato es la contratación de los artistas que con motivo de la celebración de las FESTES DE SANT JAUME 2022 actuarán los días 21, 24 y 25 de julio de 2022.   
...                                                                                                                                                                                                                                                                                                                                                ...   
179995                                                                                                                Definir las características de una calculadora portátil de tamaño bolsillo diversas funciones de cálculo. Se utilizarán por el personal de los Centros a los que se atiende desde Departamento de Seguridad del Gobierno V asco.   
179996                                                                                 El objeto del presente contrato es el servicio para el manejo de los equipos técnicos con los que se encuentran dotado el Espacio Turina para para cubrir las necesidades técnicas que demanden las distintas compañías y grupos que actuarán en dicho espa